<a href="https://colab.research.google.com/github/YHWOO13/JBNU-2017-Fall/blob/master/Thesis/%5BPlausbile_or_not%5D_Reliability_of_relation_in_KG_cuML.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Explore the relation reliability with hopping (Enhanced contextualized)

In [ ]:
%%capture
!pip install pykeen
!pip install permetrics
!git clone https://github.com/rapidsai/rapidsai-csp-utils.git
!python rapidsai-csp-utils/colab/pip-install.py

In [ ]:
import cuml
cuml.__version__

'25.04.00'

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import requests
import networkx as nx
import numpy as np
import pandas as pd
import pykeen
import torch
import json
import random
import torch.nn.functional as F
import matplotlib as plt
import time
import cupy as cp

# from sklearn.cluster import KMeans
# from sklearn.metrics import silhouette_score
from sklearn.metrics import normalized_mutual_info_score
from sklearn.decomposition import PCA
from sklearn.preprocessing import StandardScaler
from sklearn.manifold import TSNE
from sklearn.preprocessing import LabelEncoder

from pykeen.pipeline import pipeline
from collections import Counter
from collections import defaultdict
from permetrics import ClusteringMetric

from cuml.cluster import KMeans
from cuml.metrics.cluster import silhouette_samples, silhouette_score

import matplotlib.pyplot as plt


from tqdm import tqdm
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from sentence_transformers import SentenceTransformer
from pykeen.pipeline import pipeline
from pykeen.triples import TriplesFactory

INFO:pykeen.utils:Using opt_einsum


In [ ]:
import torch
device = "cuda" if torch.cuda.is_available() else "cpu"

In [ ]:
# Get the mapping of entities to their IDs
entity_to_id = umls.entity_to_id
relaton_to_id = umls.relation_to_id
# List all entities
umls_entities = list(entity_to_id.keys())
print(f"Number of entities: {len(umls_entities)}")
print("Entities:", umls_entities)

umls_relations = list(relaton_to_id.keys())
print(f"Number of relations: {len(umls_relations)}")
print("Relations:", umls_relations)


Number of entities: 135
Entities: ['acquired_abnormality', 'activity', 'age_group', 'alga', 'amino_acid_peptide_or_protein', 'amino_acid_sequence', 'amphibian', 'anatomical_abnormality', 'anatomical_structure', 'animal', 'antibiotic', 'archaeon', 'bacterium', 'behavior', 'biologic_function', 'biologically_active_substance', 'biomedical_occupation_or_discipline', 'biomedical_or_dental_material', 'bird', 'body_location_or_region', 'body_part_organ_or_organ_component', 'body_space_or_junction', 'body_substance', 'body_system', 'carbohydrate', 'carbohydrate_sequence', 'cell', 'cell_component', 'cell_function', 'cell_or_molecular_dysfunction', 'chemical', 'chemical_viewed_functionally', 'chemical_viewed_structurally', 'classification', 'clinical_attribute', 'clinical_drug', 'conceptual_entity', 'congenital_abnormality', 'daily_or_recreational_activity', 'diagnostic_procedure', 'disease_or_syndrome', 'drug_delivery_device', 'educational_activity', 'eicosanoid', 'element_ion_or_isotope', 'emb

# From saved existing/non-existing triples

In [ ]:
import json
with open('/content/drive/MyDrive/Colab Notebooks/Thesis/existing_list.json', 'r') as file:
    existing_lst = json.load(file)

with open('/content/drive/MyDrive/Colab Notebooks/Thesis/non_existing_list.json', 'r') as file:
    non_existing_lst = json.load(file)

with open('/content/drive/MyDrive/Colab Notebooks/Thesis/bert_predict.json', 'r') as file:
    bert_prediction_triples = json.load(file)


# Remove labels (existing/non-existing) and keep (subject, relation, object)
non_existing_triples = [item[:-1] for item in non_existing_lst]
existing_triples = [item[:-1] for item in existing_lst]

In [ ]:
from transformers import BertTokenizer, BertModel, RobertaTokenizer, RobertaModel, pipeline

import torch
from tqdm import tqdm

In [ ]:
# Load model and tokenizer (swap to Roberta* if needed)
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained('bert-base-uncased').to(device)
model.eval()  # always good practice

# tokenizer2 = RobertaTokenizer.from_pretrained('roberta-base')
# model2 = RobertaModel.from_pretrained('roberta-base').to(device)
# model2.eval()


/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


tokenizer_config.json:   0%|          | 0.00/48.0 [00:00<?, ?B/s]

vocab.txt:   0%|          | 0.00/232k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/466k [00:00<?, ?B/s]

config.json:   0%|          | 0.00/570 [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/440M [00:00<?, ?B/s]

BertModel(
  (embeddings): BertEmbeddings(
    (word_embeddings): Embedding(30522, 768, padding_idx=0)
    (position_embeddings): Embedding(512, 768)
    (token_type_embeddings): Embedding(2, 768)
    (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
    (dropout): Dropout(p=0.1, inplace=False)
  )
  (encoder): BertEncoder(
    (layer): ModuleList(
      (0-11): 12 x BertLayer(
        (attention): BertAttention(
          (self): BertSdpaSelfAttention(
            (query): Linear(in_features=768, out_features=768, bias=True)
            (key): Linear(in_features=768, out_features=768, bias=True)
            (value): Linear(in_features=768, out_features=768, bias=True)
            (dropout): Dropout(p=0.1, inplace=False)
          )
          (output): BertSelfOutput(
            (dense): Linear(in_features=768, out_features=768, bias=True)
            (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
            (dropout): Dropout(p=0.1, inplace=False

In [ ]:
unique_relations = list(set([r for _, r, _ in existing_triples]))

existing_vocab = tokenizer.get_vocab()

already_in_vocab = [r for r in unique_relations if r in existing_vocab]
newly_added = [r for r in unique_relations if r not in existing_vocab]

print("Already in vocab:", len(already_in_vocab), already_in_vocab)
print("Will be added:", len(newly_added), newly_added)



Already in vocab: 15 ['manages', 'treats', 'produces', 'measures', 'performs', 'affects', 'uses', 'isa', 'exhibits', 'contains', 'practices', 'surrounds', 'prevents', 'causes', 'indicates']
Will be added: 31 ['complicates', 'developmental_form_of', 'property_of', 'occurs_in', 'location_of', 'adjacent_to', 'issue_in', 'disrupts', 'conceptually_related_to', 'consists_of', 'diagnoses', 'method_of', 'evaluation_of', 'degree_of', 'manifestation_of', 'analyzes', 'assesses_effect_of', 'part_of', 'ingredient_of', 'interacts_with', 'conceptual_part_of', 'precedes', 'carries_out', 'associated_with', 'connected_to', 'derivative_of', 'result_of', 'process_of', 'co-occurs_with', 'interconnects', 'measurement_of']


In [ ]:
# Example sentence
sentence = "diagnostic procedure method_of occupation or discipline."
masked = "diagnostic procedure [MASK]  occupation or discipline."
template = "diagnostic procedure is a method of  occupation or discipline."
example = "antibiotic interacts_with vitamin."
example2 = "bacterium location_of vitamin."
# Tokenize manually

print("BERT")
tokens = tokenizer.tokenize(sentence)
masked_tokens = tokenizer.tokenize(masked)
template_tokens = tokenizer.tokenize(template)
example_tokens = tokenizer.tokenize(example2)

print(tokens)
print(masked_tokens)
print(template_tokens)
print(example_tokens)
# print('roberta')
# tokens2 = tokenizer2.tokenize(sentence)
# masked_tokens2 = tokenizer2.tokenize(masked)
# template_tokens2 = tokenizer2.tokenize(template)
# print(tokens2)
# print(masked_tokens2)
# print(template_tokens2)

BERT
['diagnostic', 'procedure', 'method', '_', 'of', 'occupation', 'or', 'discipline', '.']
['diagnostic', 'procedure', '[MASK]', 'occupation', 'or', 'discipline', '.']
['diagnostic', 'procedure', 'is', 'a', 'method', 'of', 'occupation', 'or', 'discipline', '.']
['bacterium', 'location', '_', 'of', 'vitamin', '.']


In [ ]:
relation_templates = {
    "adjacent_to":            "X is adjacent to Y",
    "affects":                "X affects Y",
    "analyzes":               "X analyzes Y",
    "assesses_effect_of":     "X assesses the effect of Y",
    "associated_with":        "X is associated with Y",
    "carries_out":            "X carries out Y",
    "causes":                 "X causes Y",
    "co-occurs_with":         "X co-occurs with Y",
    "complicates":            "X complicates Y",
    "conceptual_part_of":     "X is conceptually part of Y",
    "conceptually_related_to": "X is conceptually related to Y",
    "connected_to":           "X is connected to Y",
    "consists_of":            "X consists of Y",
    "contains":               "X contains Y",
    "degree_of":              "X has a degree of Y",  # (may need further refinement)
    "derivative_of":          "X is a derivative of Y",
    "developmental_form_of":  "X is a developmental form of Y",
    "diagnoses":              "X diagnoses Y",
    "disrupts":               "X disrupts Y",
    "evaluation_of":          "X is an evaluation of Y",
    "exhibits":               "X exhibits Y",
    "indicates":              "X indicates Y",
    "ingredient_of":          "X is an ingredient of Y",
    "interacts_with":         "X interacts with Y",
    "interconnects":          "X interconnects Y",
    "isa":                    "X is a Y",
    "issue_in":               "X is an issue in Y",
    "location_of":            "X is the location of Y",
    "manages":                "X manages Y",
    "manifestation_of":       "X is a manifestation of Y",
    "measurement_of":         "X is a measurement of Y",
    "measures":               "X measures Y",
    "method_of":              "X is a method of Y",
    "occurs_in":              "X occurs in Y",
    "part_of":                "X is a part of Y",
    "performs":               "X performs Y",
    "practices":              "X practices Y",
    "precedes":               "X precedes Y",
    "prevents":               "X prevents Y",
    "process_of":             "X is a process of Y",
    "produces":               "X produces Y",
    "property_of":            "X is a property of Y",
    "result_of":              "X is a result of Y",
    "surrounds":              "X surrounds Y",
    "treats":                 "X treats Y",
    "uses":                   "X uses Y"
}

# 040

# Think of "method_of" like a multi-word expression. We want the combined meaning, not just one word.

Averaging is a quick way to approximate:

"What is the overall semantic signal of this phrase, in this specific sentence?"

And BERT already encodes the context for both words — so averaging them tends to give a very reasonable and usable representation.

In [ ]:
relation_labels = [r for _, r, _ in existing_triples]

Relations = set(list(relation_labels))

relations = [r for r in Relations if r != 'isa']  # Exclude 'isa'

print(len(relations))


# Step 1: Keep only relations with <2 underscores
core_rel_relations = [r for r in relations if r.count('_') < 2]
two_underline_relations = [r for r in relations if r.count('_') >= 2]

# Step 2: Keep only triples with those relations
full_triples = [t for t in existing_triples if t[1] in relations]
core_rel_triples = [t for t in existing_triples if t[1] in core_rel_relations]
revised_triples = [t for t in existing_triples if t[1] in two_underline_relations]

print('core_rel_relations', len(core_rel_relations), core_rel_relations)
print('two_underline_relations', two_underline_relations)
print('core_rel_triples', len(core_rel_triples))
print(len(revised_triples))
print(len(full_triples))

45
core_rel_relations 41 ['co-occurs_with', 'ingredient_of', 'result_of', 'exhibits', 'analyzes', 'manifestation_of', 'prevents', 'location_of', 'degree_of', 'contains', 'complicates', 'method_of', 'carries_out', 'consists_of', 'diagnoses', 'connected_to', 'precedes', 'treats', 'interacts_with', 'indicates', 'practices', 'interconnects', 'uses', 'manages', 'evaluation_of', 'produces', 'measures', 'issue_in', 'performs', 'disrupts', 'causes', 'part_of', 'process_of', 'associated_with', 'surrounds', 'measurement_of', 'derivative_of', 'property_of', 'occurs_in', 'adjacent_to', 'affects']
two_underline_relations ['conceptual_part_of', 'assesses_effect_of', 'developmental_form_of', 'conceptually_related_to']
core_rel_triples 5940
89
6029


In [ ]:
'''
masked = f"{s_clean} [MASK] {o_clean}."

rel: method_of
tokens_mask ['[CLS]', 'diagnostic', 'procedure', '[MASK]', 'occupation', 'or', 'discipline', '.', '[SEP]', '[PAD]']
mask_indices [3]

rel: affects
tokens_mask ['[CLS]', 'molecular', 'biology', 'research', 'technique', '[MASK]', 'mental', 'process', '.', '[SEP]']
mask_indices [5]

rel: result_of
tokens_mask ['[CLS]', 'mental', 'process', '[MASK]', 'behavior', '.', '[SEP]', '[PAD]', '[PAD]', '[PAD]']
mask_indices [3]

rel: affects
tokens_mask ['[CLS]', 'research', 'activity', '[MASK]', 'mental', 'process', '.', '[SEP]', '[PAD]', '[PAD]']
mask_indices [3]

'''

# Full Relation & Masking

In [ ]:
def extract_relation_embeddings(
    triples, tokenizer, model, batch_size=128, device="cuda"
):
    """
    Extracts full and masked embeddings for relation triples.

    Args:
        triples (list of tuples): List of (subject, relation, object) triples.
        tokenizer: HuggingFace tokenizer.
        model: HuggingFace transformer model.
        batch_size (int): Batch size for processing.
        device (str): Device to run model on ("cuda" or "cpu").

    Returns:
        X_full (list): Embeddings for unmasked (full) relations.
        X_masked (list): Embeddings for masked relations.
        y (list): List of relation labels.
    """
    def clean_text(text):
        return text.replace("_", " ")

    X_full, X_masked, y = [], [], []

    for i in tqdm(range(0, len(triples), batch_size), desc="Extracting embeddings"):
        batch = triples[i:i + batch_size]

        sent_list = []
        mask_list = []
        rel_list = []

        for s, rel, o in batch:
            s_clean = clean_text(s)
            o_clean = clean_text(o)
            full_rel = rel.replace("_", " ")
            sent = f"{s_clean} {full_rel} {o_clean}."
            masked = f"{s_clean} [MASK] {o_clean}."

            sent_list.append(sent)
            mask_list.append(masked)
            rel_list.append(rel)

        inputs_sent = tokenizer(sent_list, padding=True, truncation=True, return_tensors="pt").to(device)
        inputs_mask = tokenizer(mask_list, padding=True, truncation=True, return_tensors="pt").to(device)

        with torch.no_grad():
            outputs_sent = model(**inputs_sent)
            outputs_mask = model(**inputs_mask)

        for idx, rel in enumerate(rel_list):
            rel_tokens = tokenizer.tokenize(rel.replace("_", " "))
            rel_token_ids = tokenizer.convert_tokens_to_ids(rel_tokens)

            input_ids = inputs_sent["input_ids"][idx]
            tokens = tokenizer.convert_ids_to_tokens(input_ids.cpu().tolist())

            # Find relation token span in full sentence
            match_indices = []
            for j in range(len(tokens) - len(rel_token_ids) + 1):
                if input_ids[j+1:j+1+len(rel_token_ids)].tolist() == rel_token_ids:
                    match_indices = list(range(j+1, j+1+len(rel_token_ids)))
                    break

            if match_indices:
                emb_full = outputs_sent.last_hidden_state[idx, match_indices, :].mean(dim=0).detach().cpu().numpy()
                X_full.append(emb_full)

            # Extract masked embedding
            input_ids_mask = inputs_mask["input_ids"][idx]
            tokens_mask = tokenizer.convert_ids_to_tokens(input_ids_mask.cpu().tolist())
            mask_indices = [k for k, tok in enumerate(tokens_mask) if tok == "[MASK]"]

            if mask_indices:
                emb_masked = outputs_mask.last_hidden_state[idx, mask_indices, :].mean(dim=0).detach().cpu().numpy()
                X_masked.append(emb_masked)

            y.append(rel)

    return X_full, X_masked, y

In [ ]:
print(len(y))

6029


# Core relation

In [ ]:
def extract_core_relation_embeddings(
    triples, tokenizer, model, batch_size=128, device="cuda"
):
    """
    Extracts embeddings for core relations only (e.g., first token in a relation string).

    Args:
        triples (list of tuples): List of (subject, relation, object) triples.
        tokenizer: HuggingFace tokenizer.
        model: HuggingFace transformer model.
        batch_size (int): Batch size for processing.
        device (str): Device to run model on ("cuda" or "cpu").

    Returns:
        X_core (list): Core relation embeddings.
        y_core (list): Corresponding relation labels.
    """
    def clean_text(text):
        return text.replace("_", " ")

    X_core = []
    y_core = []

    print('core_rel_triples:', len(triples))

    for i in tqdm(range(0, len(triples), batch_size), desc="Processing core_rel_triples in batches"):
        batch = triples[i:i + batch_size]

        sent_list = []
        rel_list = []

        for s, rel, o in batch:
            s_clean = clean_text(s)
            o_clean = clean_text(o)
            core_rel = rel.split("_")[0]
            sent = f"{s_clean} {core_rel} {o_clean}."

            sent_list.append(sent)
            rel_list.append(core_rel)

        # Tokenize the batch
        inputs = tokenizer(sent_list, padding=True, truncation=True, return_tensors="pt").to(device)

        with torch.no_grad():
            outputs = model(**inputs)

        for idx, core_rel in enumerate(rel_list):
            rel_token_ids = tokenizer.convert_tokens_to_ids(tokenizer.tokenize(core_rel))
            input_ids = inputs["input_ids"][idx]
            tokens = tokenizer.convert_ids_to_tokens(input_ids.cpu().tolist())

            match_indices = []
            for j in range(len(tokens) - len(rel_token_ids) + 1):
                if input_ids[j+1:j+1+len(rel_token_ids)].tolist() == rel_token_ids:
                    match_indices = list(range(j+1, j+1+len(rel_token_ids)))
                    break

            if match_indices:
                embedding_core = outputs.last_hidden_state[idx, match_indices, :].mean(dim=0).detach().cpu().numpy()
                X_core.append(embedding_core)
                y_core.append(rel_list[idx])

    return X_core, y_core

# Calculate NMI, Purity score for Full relation / Core relaiton / Masking

In [ ]:
# Step 4: Clustering Evaluation Function
def evaluate_embeddings(embeddings, labels, label_ids, title=""):
    embeddings_gpu = cp.asarray(embeddings)
    num_clusters = len(set(label_ids))

    kmeans = KMeans(n_clusters=num_clusters, random_state=42, max_iter=300)
    kmeans.fit(embeddings_gpu)
    cluster_labels = kmeans.labels_

    # Convert to CPU numpy
    cluster_labels_np = cluster_labels.get()

    # NMI
    nmi = normalized_mutual_info_score(label_ids, cluster_labels_np)

    # Purity (using your ClusteringMetric class)
    cm = ClusteringMetric(label_ids, cluster_labels_np)
    purity = cm.purity_score()

    # Silhouette
    # sil_score = silhouette_score(embeddings_gpu, cluster_labels_np)

    print(f"[{title}] NMI: {nmi:.4f}")
    print(f"[{title}] Purity: {purity:.4f}")
    # print(f"[{title}] Silhouette: {sil_score:.4f}\n")

    return nmi, purity



X_full, X_masked, y = extract_relation_embeddings(
    triples = full_triples,
    tokenizer = tokenizer,
    model = model,
    batch_size=128,
    device="cuda"
)

X_core, y_core = extract_core_relation_embeddings(
    triples=core_rel_triples,
    tokenizer=tokenizer,
    model=model,
    batch_size=128,
    device="cuda"
)

# Step 3: Label encoding
label_encoder = LabelEncoder()

label_ids = label_encoder.fit_transform(y)
core_label_ids = label_encoder.fit_transform(y_core)

print('label_ids', len(label_ids))
print('core_label_ids', len(core_label_ids))
print("")

# Step 5: Run Evaluation
evaluate_embeddings(X_full, y, label_ids, title="Full Relation")
print("")
evaluate_embeddings(X_core, y_core, core_label_ids, title="Core Relation Only")

print("")
evaluate_embeddings(X_masked, y, label_ids, title="Masked Relation")
print("")

Extracting embeddings: 100%|██████████| 48/48 [00:10<00:00,  4.72it/s]


core_rel_triples: 5940


Processing core_rel_triples in batches: 100%|██████████| 47/47 [00:05<00:00,  8.38it/s]


label_ids 6029
core_label_ids 5940

[Full Relation] NMI: 0.8521
[Full Relation] Purity: 0.6374

[Core Relation Only] NMI: 0.8870
[Core Relation Only] Purity: 0.6806

[Masked Relation] NMI: 0.3581
[Masked Relation] Purity: 0.2355



/usr/local/lib/python3.11/dist-packages/cuml/internals/api_decorators.py:195: FutureWarning: The default value of `n_init` will change from 1 to 'auto' in 25.04. Set the value of `n_init` explicitly to suppress this warning.
  return func(*args, **kwargs)
/usr/local/lib/python3.11/dist-packages/cuml/internals/api_decorators.py:195: FutureWarning: The default value of `n_init` will change from 1 to 'auto' in 25.04. Set the value of `n_init` explicitly to suppress this warning.
  return func(*args, **kwargs)
/usr/local/lib/python3.11/dist-packages/cuml/internals/api_decorators.py:195: FutureWarning: The default value of `n_init` will change from 1 to 'auto' in 25.04. Set the value of `n_init` explicitly to suppress this warning.
  return func(*args, **kwargs)


# Existing + Non-existing Triples

In [ ]:
all_triples = existing_triples + non_existing_triples
print(len(all_triples))

838350


In [ ]:
all_triples_relation_labels = [r for _, r, _ in all_triples]

all_triples_Relations = set(list(all_triples_relation_labels))

all_triples_relations = [r for r in all_triples_Relations if r != 'isa']  # Exclude 'isa'

print(len(all_triples_relations))


# Step 1: Keep only relations with <2 underscores
all_triple_core_rel_relations = [r for r in all_triples_relations if r.count('_') < 2]
all_triples_two_underline_relations = [r for r in all_triples_relations if r.count('_') >= 2]

# # Step 2: Keep only triples with those relations
at_full_triples = [t for t in all_triples if t[1] in all_triples_relations]
at_core_rel_triples = [t for t in all_triples if t[1] in all_triple_core_rel_relations]
# revised_triples = [t for t in existing_triples if t[1] in two_underline_relations]

# print('core_rel_relations', len(core_rel_relations), core_rel_relations)
print('all_triples_two_underline_relations', len(all_triples_two_underline_relations))
print('at_core_rel_triples', len(at_core_rel_triples))
# print(len(revised_triples))
print('at_full_triples', len(at_full_triples))

45
all_triples_two_underline_relations 4
at_core_rel_triples 747225
at_full_triples 820125


In [ ]:
non_existing_triples_relation_labels = [r for _, r, _ in non_existing_triples]

non_existing_triples_Relations = set(list(non_existing_triples_relation_labels))

non_existing_triples_relations = [r for r in non_existing_triples_Relations if r != 'isa']  # Exclude 'isa'

print('non_existing_triples_relations', len(non_existing_triples_relations))


# Step 1: Keep only relations with <2 underscores
non_existing_core_rel_relations = [r for r in non_existing_triples_relations if r.count('_') < 2]
non_existing_two_underline_relations = [r for r in non_existing_triples_relations if r.count('_') >= 2]

# # Step 2: Keep only triples with those relations
ne_full_triples = [t for t in non_existing_triples if t[1] in non_existing_triples_relations]
ne_core_rel_triples = [t for t in non_existing_triples if t[1] in non_existing_core_rel_relations]
# revised_triples = [t for t in existing_triples if t[1] in two_underline_relations]

print('non_existing_core_rel_relations', len(non_existing_core_rel_relations))#, non_existing_core_rel_relations)
# print('all_triples_two_underline_relations', len(all_triples_two_underline_relations))
print('ne_core_rel_triples', len(ne_core_rel_triples))
# print(len(revised_triples))
print('ne_full_triples', len(ne_full_triples))

non_existing_triples_relations 45
non_existing_core_rel_relations 41
ne_core_rel_triples 741285
ne_full_triples 814096


In [ ]:
def extract_relation_embeddings(
    triples, tokenizer, model, batch_size=128, device="cuda"
):
    """
    Extracts full and masked embeddings for relation triples.

    Args:
        triples (list of tuples): List of (subject, relation, object) triples.
        tokenizer: HuggingFace tokenizer.
        model: HuggingFace transformer model.
        batch_size (int): Batch size for processing.
        device (str): Device to run model on ("cuda" or "cpu").

    Returns:
        X_full (list): Embeddings for unmasked (full) relations.
        X_masked (list): Embeddings for masked relations.
        y (list): List of relation labels.
    """

    def clean_text(text):
        return text.replace("_", " ")

    X, y = [], []

    for i in tqdm(range(0, len(triples), batch_size), desc="Extracting embeddings"):
        batch = triples[i:i + batch_size]

        sent_list = []
        rel_list = []

        for s, rel, o in batch:
            s_clean = clean_text(s)
            o_clean = clean_text(o)
            full_rel = rel.replace("_", " ")

            sent = f"{s_clean} {full_rel} {o_clean}."

            sent_list.append(sent)
            rel_list.append(rel)

        inputs_sent = tokenizer(sent_list, padding=True, truncation=True, return_tensors="pt").to(device)

        with torch.no_grad():
            outputs_sent = model(**inputs_sent)

        for idx, rel in enumerate(rel_list):
          # print('idx:', idx, 'rel:', rel)
          rel_tokens = tokenizer.tokenize(rel.replace("_", " "))
          rel_token_ids = tokenizer.convert_tokens_to_ids(rel_tokens)

          input_ids = inputs_sent["input_ids"][idx]
          tokens = tokenizer.convert_ids_to_tokens(input_ids.cpu().tolist())

          # Find relation token span in full sentence
          match_indices = []
          for j in range(len(tokens) - len(rel_token_ids) + 1):
              if input_ids[j+1:j+1+len(rel_token_ids)].tolist() == rel_token_ids:
                  match_indices = list(range(j+1, j+1+len(rel_token_ids)))
                  break
          if match_indices:
              emb_full = outputs_sent.last_hidden_state[idx, match_indices, :].mean(dim=0).detach().cpu().numpy()
              X.append(emb_full)


          y.append(rel)

    return X, y


# X_full, y_full = extract_relation_embeddings(
#     triples = full_triples,
#     tokenizer = tokenizer,
#     model = model,
#     batch_size=128,
#     device="cuda"
# )

#0705 Analyze whether the non-existing triples are plausible or not

In [ ]:
# === MAIN EXECUTION ===

# 1. Define triples
all_triples = full_triples + ne_full_triples  # replace bert_prediction_triples with non_existing_triples

# 2. Extract embeddings
all_X_full, all_y_full = extract_relation_embeddings(
    triples=all_triples,
    tokenizer=tokenizer,
    model=model,
    batch_size=128,
    device="cuda"
)

all_X_full_np = np.array(all_X_full)

Extracting embeddings:  44%|████▍     | 2847/6408 [05:51<07:19,  8.10it/s]


KeyboardInterrupt: 

In [ ]:
# 3. Cluster into gold-standard number of clusters (e.g., 45)
kmeans = KMeans(n_clusters=45, random_state=42)
cluster_labels = kmeans.fit_predict(all_X_full_np)
cluster_centroids = kmeans.cluster_centers_

# Extract relations from full_triples
full_triples_relations = [triple[1] for triple in full_triples]

# 4. Map clusters to existing triples to find representative relations
true_cluster_to_counts = defaultdict(Counter)
for label, rel in zip(cluster_labels[:len(full_triples)], full_triples_relations):  # Only existing triples
    true_cluster_to_counts[label][rel] += 1

representative_rels = {}
for cluster_id, rel_counter in sorted(true_cluster_to_counts.items()):
    most_common_rel, count = rel_counter.most_common(1)[0]
    representative_rels[cluster_id] = most_common_rel
    print(f"Cluster {cluster_id} ➝ Representative: {most_common_rel} (Count: {count})")

# 5. Check plausibility for non-existing triples
plausible_count = 0
non_existing_start_idx = len(full_triples)

for i, (triple, label) in enumerate(zip(non_existing_triples, cluster_labels[non_existing_start_idx:]), start=non_existing_start_idx):
    non_existing_rel = triple[1]  # relation of non-existing triple
    representative_rel = representative_rels.get(label, None)
    if representative_rel == non_existing_rel:
        plausible_count += 1
        print(f"[Plausible] Triple: {triple} in Cluster {label} ➝ Representative: {representative_rel}")
    else:
        print(f"[Not Plausible] Triple: {triple} in Cluster {label} ➝ Representative: {representative_rel}")

print(f"\nTotal plausible non-existing triples: {plausible_count} out of {len(non_existing_triples)}")

#0705 Sampling

In [ ]:
n_rounds = 5
plausible_counts = []

for i in range(n_rounds):
    print(f"\n=== Evaluation Round {i+1} ===")

    # Step 1: Sample non-existing triples to match existing count
    sampled_negatives = random.sample(ne_full_triples, len(full_triples))

    # Combine existing + sampled non-existing triples
    combined_triples = full_triples + sampled_negatives

    # Step 2: Extract embeddings
    X, y = extract_relation_embeddings(
        triples=combined_triples,
        tokenizer=tokenizer,
        model=model,
        batch_size=128,
        device="cuda"
    )

    X_np = np.array(X)

    # Step 3: Cluster using gold-standard number of clusters (e.g. 45)
    kmeans = KMeans(n_clusters=45, random_state=42)
    cluster_labels = kmeans.fit_predict(X_np)

    # Step 4: Map clusters to existing triples to find representative relations
    full_triples_relations = [triple[1] for triple in full_triples]

    true_cluster_to_counts = defaultdict(Counter)
    for label, rel in zip(cluster_labels[:len(full_triples)], full_triples_relations):
        true_cluster_to_counts[label][rel] += 1

    representative_rels = {}
    for cluster_id, rel_counter in sorted(true_cluster_to_counts.items()):
        most_common_rel, count = rel_counter.most_common(1)[0]
        representative_rels[cluster_id] = most_common_rel
        print(f"Cluster {cluster_id} ➝ Representative: {most_common_rel} (Count: {count})")

    # Step 5: Check plausibility for sampled non-existing triples
    plausible_count = 0
    non_existing_start_idx = len(full_triples)

    for triple, label in zip(sampled_negatives, cluster_labels[non_existing_start_idx:]):
        non_existing_rel = triple[1]
        representative_rel = representative_rels.get(label, None)
        if representative_rel == non_existing_rel:
            plausible_count += 1
            print(f"[Plausible] Triple: {triple} in Cluster {label} ➝ Representative: {representative_rel}")
        else:
            print(f"[Not Plausible] Triple: {triple} in Cluster {label} ➝ Representative: {representative_rel}")

    print(f"Round {i+1} ➝ Total plausible non-existing triples: {plausible_count} out of {len(sampled_negatives)}")
    plausible_counts.append(plausible_count / len(sampled_negatives))  # store as proportion

# === Final aggregated metrics ===
print(f"\nAverage plausible ratio: {np.mean(plausible_counts):.4f} ± {np.std(plausible_counts):.4f}")


=== Evaluation Round 1 ===


Extracting embeddings: 100%|██████████| 95/95 [00:11<00:00,  8.10it/s]


Cluster 0 ➝ Representative: location_of (Count: 300)
Cluster 1 ➝ Representative: disrupts (Count: 154)
Cluster 2 ➝ Representative: process_of (Count: 421)
Cluster 3 ➝ Representative: treats (Count: 2)
Cluster 4 ➝ Representative: produces (Count: 195)
Cluster 5 ➝ Representative: complicates (Count: 263)
Cluster 6 ➝ Representative: interacts_with (Count: 164)
Cluster 7 ➝ Representative: interconnects (Count: 2)
Cluster 8 ➝ Representative: performs (Count: 90)
Cluster 9 ➝ Representative: result_of (Count: 280)
Cluster 10 ➝ Representative: issue_in (Count: 268)
Cluster 11 ➝ Representative: contains (Count: 11)
Cluster 12 ➝ Representative: carries_out (Count: 38)
Cluster 13 ➝ Representative: analyzes (Count: 52)
Cluster 14 ➝ Representative: affects (Count: 273)
Cluster 15 ➝ Representative: exhibits (Count: 1)
Cluster 16 ➝ Representative: interacts_with (Count: 287)
Cluster 17 ➝ Representative: manifestation_of (Count: 179)
Cluster 18 ➝ Representative: diagnoses (Count: 48)
Cluster 19 ➝ Repr

Extracting embeddings: 100%|██████████| 95/95 [00:11<00:00,  8.11it/s]


Cluster 0 ➝ Representative: exhibits (Count: 45)
Cluster 1 ➝ Representative: location_of (Count: 302)
Cluster 2 ➝ Representative: affects (Count: 283)
Cluster 3 ➝ Representative: co-occurs_with (Count: 67)
Cluster 4 ➝ Representative: result_of (Count: 298)
Cluster 5 ➝ Representative: produces (Count: 216)
Cluster 6 ➝ Representative: indicates (Count: 2)
Cluster 7 ➝ Representative: measures (Count: 24)
Cluster 8 ➝ Representative: analyzes (Count: 52)
Cluster 9 ➝ Representative: affects (Count: 402)
Cluster 10 ➝ Representative: causes (Count: 330)
Cluster 11 ➝ Representative: prevents (Count: 32)
Cluster 12 ➝ Representative: developmental_form_of (Count: 4)
Cluster 13 ➝ Representative: result_of (Count: 280)
Cluster 14 ➝ Representative: uses (Count: 48)
Cluster 15 ➝ Representative: occurs_in (Count: 89)
Cluster 16 ➝ Representative: complicates (Count: 160)
Cluster 17 ➝ Representative: issue_in (Count: 268)
Cluster 18 ➝ Representative: process_of (Count: 418)
Cluster 19 ➝ Representative: 

...

Cluster 0 ➝ Representative: derivative_of (Count: 1)
Cluster 1 ➝ Representative: affects (Count: 404)
Cluster 2 ➝ Representative: associated_with (Count: 26)
Cluster 3 ➝ Representative: analyzes (Count: 52)
Cluster 4 ➝ Representative: complicates (Count: 163)
Cluster 5 ➝ Representative: contains (Count: 11)
Cluster 6 ➝ Representative: developmental_form_of (Count: 4)
Cluster 7 ➝ Representative: part_of (Count: 197)
Cluster 8 ➝ Representative: interacts_with (Count: 288)
Cluster 9 ➝ Representative: co-occurs_with (Count: 67)
Cluster 10 ➝ Representative: prevents (Count: 32)
Cluster 11 ➝ Representative: indicates (Count: 27)
Cluster 12 ➝ Representative: issue_in (Count: 268)
Cluster 13 ➝ Representative: manifestation_of (Count: 169)
Cluster 14 ➝ Representative: measures (Count: 148)
Cluster 15 ➝ Representative: performs (Count: 88)
Cluster 16 ➝ Representative: produces (Count: 276)
Cluster 17 ➝ Representative: process_of (Count: 421)
Cluster 18 ➝ Representative: precedes (Count: 73)
Clus

Extracting embeddings: 100%|██████████| 95/95 [00:11<00:00,  7.98it/s]


Cluster 0 ➝ Representative: developmental_form_of (Count: 4)
Cluster 1 ➝ Representative: occurs_in (Count: 72)
Cluster 2 ➝ Representative: process_of (Count: 255)
Cluster 3 ➝ Representative: causes (Count: 109)
Cluster 4 ➝ Representative: affects (Count: 450)
Cluster 5 ➝ Representative: co-occurs_with (Count: 67)
Cluster 6 ➝ Representative: affects (Count: 501)
Cluster 7 ➝ Representative: complicates (Count: 263)
Cluster 8 ➝ Representative: part_of (Count: 197)
Cluster 9 ➝ Representative: measurement_of (Count: 64)
Cluster 10 ➝ Representative: uses (Count: 17)
Cluster 11 ➝ Representative: associated_with (Count: 14)
Cluster 12 ➝ Representative: produces (Count: 276)
Cluster 13 ➝ Representative: indicates (Count: 27)
Cluster 14 ➝ Representative: performs (Count: 90)
Cluster 15 ➝ Representative: process_of (Count: 182)
Cluster 16 ➝ Representative: practices (Count: 2)
Cluster 17 ➝ Representative: diagnoses (Count: 48)
Cluster 18 ➝ Representative: surrounds (Count: 8)
Cluster 19 ➝ Represe

Extracting embeddings: 100%|██████████| 95/95 [00:11<00:00,  8.07it/s]


Cluster 0 ➝ Representative: assesses_effect_of (Count: 65)
Cluster 1 ➝ Representative: result_of (Count: 280)
Cluster 2 ➝ Representative: co-occurs_with (Count: 67)
Cluster 3 ➝ Representative: process_of (Count: 403)
Cluster 4 ➝ Representative: associated_with (Count: 64)
Cluster 5 ➝ Representative: affects (Count: 358)
Cluster 6 ➝ Representative: produces (Count: 276)
Cluster 7 ➝ Representative: adjacent_to (Count: 7)
Cluster 8 ➝ Representative: location_of (Count: 299)
Cluster 9 ➝ Representative: complicates (Count: 263)
Cluster 10 ➝ Representative: affects (Count: 177)
Cluster 11 ➝ Representative: practices (Count: 2)
Cluster 12 ➝ Representative: measures (Count: 31)
Cluster 13 ➝ Representative: conceptual_part_of (Count: 16)
Cluster 14 ➝ Representative: result_of (Count: 296)
Cluster 15 ➝ Representative: issue_in (Count: 268)
Cluster 16 ➝ Representative: manages (Count: 6)
Cluster 17 ➝ Representative: uses (Count: 65)
Cluster 18 ➝ Representative: occurs_in (Count: 90)
Cluster 19 ➝ 

## Dominant-based approach

In [ ]:
# === Step 1. Extract existing triple embeddings ===
existing_X, existing_y = extract_relation_embeddings(
    triples=full_triples,
    tokenizer=tokenizer,
    model=model,
    batch_size=128,
    device="cuda"
)
existing_X_np = np.array(existing_X)
full_triples_relations = [triple[1] for triple in full_triples]

# === Step 2. Cluster existing triples ===
kmeans = KMeans(n_clusters=45, random_state=42)
kmeans.fit(existing_X_np)

# === Step 3. Map clusters to representative relations ===
true_cluster_to_counts = defaultdict(Counter)
cluster_labels_existing = kmeans.labels_

for label, rel in zip(cluster_labels_existing, full_triples_relations):
    true_cluster_to_counts[label][rel] += 1

representative_rels = {}
for cluster_id, rel_counter in sorted(true_cluster_to_counts.items()):
    most_common_rel, count = rel_counter.most_common(1)[0]
    representative_rels[cluster_id] = most_common_rel
    print(f"Cluster {cluster_id} ➝ Representative: {most_common_rel} (Count: {count})")

# === Step 4. Extract non-existing triple embeddings ===
non_existing_X, non_existing_y = extract_relation_embeddings(
    triples=ne_full_triples,
    tokenizer=tokenizer,
    model=model,
    batch_size=128,
    device="cuda"
)
non_existing_X_np = np.array(non_existing_X)

# === Step 5. Predict cluster assignment for non-existing triples ===
predicted_labels_non_existing = kmeans.predict(non_existing_X_np)

# === Step 6. Check plausibility for non-existing triples ===
plausible_count = 0

for triple, label in zip(ne_full_triples, predicted_labels_non_existing):
    non_existing_rel = triple[1]  # relation of non-existing triple
    representative_rel = representative_rels.get(label, None)

    if representative_rel == non_existing_rel:
        plausible_count += 1
        print(f"[Plausible] Triple: {triple} in Cluster {label} ➝ Representative: {representative_rel}")
    else:
        print(f"[Not Plausible] Triple: {triple} in Cluster {label} ➝ Representative: {representative_rel}")

print(f"\nTotal plausible non-existing triples: {plausible_count} out of {len(ne_full_triples)}")


Extracting embeddings: 100%|██████████| 48/48 [00:05<00:00,  8.21it/s]


Cluster 0 ➝ Representative: affects (Count: 106)
Cluster 1 ➝ Representative: location_of (Count: 299)
Cluster 2 ➝ Representative: affects (Count: 115)
Cluster 3 ➝ Representative: assesses_effect_of (Count: 65)
Cluster 4 ➝ Representative: causes (Count: 200)
Cluster 5 ➝ Representative: produces (Count: 226)
Cluster 6 ➝ Representative: complicates (Count: 146)
Cluster 7 ➝ Representative: affects (Count: 214)
Cluster 8 ➝ Representative: result_of (Count: 160)
Cluster 9 ➝ Representative: process_of (Count: 140)
Cluster 10 ➝ Representative: interacts_with (Count: 105)
Cluster 11 ➝ Representative: issue_in (Count: 268)
Cluster 12 ➝ Representative: measures (Count: 80)
Cluster 13 ➝ Representative: performs (Count: 90)
Cluster 14 ➝ Representative: result_of (Count: 151)
Cluster 15 ➝ Representative: disrupts (Count: 154)
Cluster 16 ➝ Representative: part_of (Count: 197)
Cluster 17 ➝ Representative: interacts_with (Count: 16)
Cluster 18 ➝ Representative: produces (Count: 50)
Cluster 19 ➝ Represe

Extracting embeddings: 100%|██████████| 6361/6361 [13:09<00:00,  8.06it/s]


Streaming output truncated to the last 5000 lines.
[Not Plausible] Triple: ['mental_process', 'analyzes', 'geographic_area'] in Cluster 3 ➝ Representative: assesses_effect_of
[Not Plausible] Triple: ['professional_society', 'diagnoses', 'conceptual_entity'] in Cluster 3 ➝ Representative: assesses_effect_of
[Not Plausible] Triple: ['amphibian', 'conceptual_part_of', 'neuroreactive_substance_or_biogenic_amine'] in Cluster 21 ➝ Representative: property_of
[Not Plausible] Triple: ['functional_concept', 'diagnoses', 'bird'] in Cluster 3 ➝ Representative: assesses_effect_of
[Plausible] Triple: ['rickettsia_or_chlamydia', 'performs', 'body_substance'] in Cluster 13 ➝ Representative: performs
[Not Plausible] Triple: ['organism', 'adjacent_to', 'laboratory_or_test_result'] in Cluster 17 ➝ Representative: interacts_with
[Plausible] Triple: ['body_location_or_region', 'uses', 'functional_concept'] in Cluster 33 ➝ Representative: uses
[Not Plausible] Triple: ['fish', 'connected_to', 'regulation_or

## Lenient inclusion-based approach

In [ ]:
# === Step 1. Extract existing triple embeddings ===
existing_X, existing_y = extract_relation_embeddings(
    triples=full_triples,
    tokenizer=tokenizer,
    model=model,
    batch_size=128,
    device="cuda"
)
existing_X_np = np.array(existing_X)
full_triples_relations = [triple[1] for triple in full_triples]

# === Step 2. Cluster existing triples ===
kmeans = KMeans(n_clusters=45, random_state=42)
kmeans.fit(existing_X_np)

# === Step 3. Map clusters to ALL contained relations (not just representative) ===
true_cluster_to_counts = defaultdict(Counter)
cluster_labels_existing = kmeans.labels_

for label, rel in zip(cluster_labels_existing, full_triples_relations):
    true_cluster_to_counts[label][rel] += 1

# === Optional: print detailed counts for each cluster ===
for cluster_id, rel_counter in sorted(true_cluster_to_counts.items()):
    print(f"\nCluster {cluster_id} (Existing Relations):")
    for rel, count in rel_counter.most_common():
        print(f"  {rel}: {count}")

# === Step 4. Extract non-existing triple embeddings ===
non_existing_X, non_existing_y = extract_relation_embeddings(
    triples=ne_full_triples,
    tokenizer=tokenizer,
    model=model,
    batch_size=128,
    device="cuda"
)
non_existing_X_np = np.array(non_existing_X)

# === Step 5. Predict cluster assignment for non-existing triples ===
predicted_labels_non_existing = kmeans.predict(non_existing_X_np)

# === Step 6. Check plausibility against ALL relations in assigned cluster ===
plausible_count = 0

for triple, label in zip(ne_full_triples, predicted_labels_non_existing):
    non_existing_rel = triple[1]  # relation of non-existing triple
    cluster_relations = true_cluster_to_counts.get(label, {})

    if non_existing_rel in cluster_relations:
        plausible_count += 1
        print(f"[Plausible] Triple: {triple} in Cluster {label} ➝ Matches existing relation(s)")
    else:
        print(f"[Not Plausible] Triple: {triple} in Cluster {label} ➝ No match among existing relations")

print(f"\nTotal plausible non-existing triples: {plausible_count} out of {len(ne_full_triples)}")


Extracting embeddings: 100%|██████████| 48/48 [00:06<00:00,  7.42it/s]



Cluster 0 (Existing Relations):
  affects: 106

Cluster 1 (Existing Relations):
  location_of: 299
  method_of: 1

Cluster 2 (Existing Relations):
  affects: 115

Cluster 3 (Existing Relations):
  assesses_effect_of: 65
  analyzes: 52
  diagnoses: 48

Cluster 4 (Existing Relations):
  causes: 200

Cluster 5 (Existing Relations):
  produces: 226

Cluster 6 (Existing Relations):
  complicates: 146

Cluster 7 (Existing Relations):
  affects: 214

Cluster 8 (Existing Relations):
  result_of: 160

Cluster 9 (Existing Relations):
  process_of: 140
  degree_of: 2

Cluster 10 (Existing Relations):
  interacts_with: 105

Cluster 11 (Existing Relations):
  issue_in: 268

Cluster 12 (Existing Relations):
  measures: 80

Cluster 13 (Existing Relations):
  performs: 90
  manages: 6
  practices: 1

Cluster 14 (Existing Relations):
  result_of: 151
  manifestation_of: 1
  location_of: 1

Cluster 15 (Existing Relations):
  disrupts: 154
  affects: 1

Cluster 16 (Existing Relations):
  part_of: 197
  

Extracting embeddings: 100%|██████████| 6361/6361 [13:04<00:00,  8.11it/s]


Streaming output truncated to the last 5000 lines.
[Plausible] Triple: ['mental_process', 'analyzes', 'geographic_area'] in Cluster 3 ➝ Matches existing relation(s)
[Plausible] Triple: ['professional_society', 'diagnoses', 'conceptual_entity'] in Cluster 3 ➝ Matches existing relation(s)
[Plausible] Triple: ['amphibian', 'conceptual_part_of', 'neuroreactive_substance_or_biogenic_amine'] in Cluster 21 ➝ Matches existing relation(s)
[Plausible] Triple: ['functional_concept', 'diagnoses', 'bird'] in Cluster 3 ➝ Matches existing relation(s)
[Plausible] Triple: ['rickettsia_or_chlamydia', 'performs', 'body_substance'] in Cluster 13 ➝ Matches existing relation(s)
[Plausible] Triple: ['organism', 'adjacent_to', 'laboratory_or_test_result'] in Cluster 17 ➝ Matches existing relation(s)
[Plausible] Triple: ['body_location_or_region', 'uses', 'functional_concept'] in Cluster 33 ➝ Matches existing relation(s)
[Plausible] Triple: ['fish', 'connected_to', 'regulation_or_law'] in Cluster 17 ➝ Matches 

In [ ]:
# Step 4: Clustering Evaluation Function
def evaluate_embeddings(embeddings, labels, label_ids, title=""):
    embeddings_gpu = cp.asarray(embeddings)
    num_clusters = len(set(label_ids))
    print("num_clusters", num_clusters)
    kmeans = KMeans(n_clusters=num_clusters, random_state=42, max_iter=300)
    kmeans.fit(embeddings_gpu)
    cluster_labels = kmeans.labels_

    # Convert to CPU numpy
    cluster_labels_np = cluster_labels.get()

    # NMI
    nmi = normalized_mutual_info_score(label_ids, cluster_labels_np)

    # Purity (using your ClusteringMetric class)
    cm = ClusteringMetric(label_ids, cluster_labels_np)
    purity = cm.purity_score()

    # Silhouette
    # sil_score = silhouette_score(embeddings_gpu, cluster_labels_np)

    print(f"[{title}] NMI: {nmi:.4f}")
    print(f"[{title}] Purity: {purity:.4f}")
    # print(f"[{title}] Silhouette: {sil_score:.4f}\n")

    return nmi, purity


# Sampling (Full triples)

In [ ]:
n_rounds = 5
nmis, purity_scores = [], []
label_encoder = LabelEncoder()

for i in range(n_rounds):
  # Step 1: Sample non-existing to balance
  sampled_negatives = random.sample(ne_full_triples, len(full_triples))
  combined_triples = full_triples + sampled_negatives
  label_ids = [0]*len(full_triples) + [1]*len(sampled_negatives)
  print(len(sampled_negatives))
  print(len(combined_triples))
  # Step 2: Get embeddings
  # embeddings = model.encode(combined_triples)  # model must return numpy array
  X, y = extract_relation_embeddings(
    triples = combined_triples,
    tokenizer = tokenizer,
    model = model,
    batch_size=128,
    device="cuda"
)

  label_ids = label_encoder.fit_transform(y)
  print(len(y))

  # Step 3: Evaluate using your provided function
  print(f"=== Evaluation Round {i+1} ===")
  nmi, purity = evaluate_embeddings(X, y, label_ids, title=f"Round {i+1}")

  # # Step 4: Optional metric collection for averaging
  # embeddings_gpu = cp.asarray(embeddings)
  # kmeans = KMeans(n_clusters=2, random_state=42)
  # kmeans.fit(embeddings_gpu)
  # cluster_labels = kmeans.labels_.get()

  # nmi = normalized_mutual_info_score(label_ids, cluster_labels)
  # cm = ClusteringMetric(label_ids, cluster_labels)
  # purity = cm.purity_score()

  nmis.append(nmi)
  purity_scores.append(purity)

# Final aggregated metrics
print(f"\nAverage NMI: {np.mean(nmis):.4f} ± {np.std(nmis):.4f}")
print(f"Average Purity: {np.mean(purity_scores):.4f} ± {np.std(purity_scores):.4f}")

6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:11<00:00,  7.94it/s]


12058
=== Evaluation Round 1 ===
[Round 1] NMI: 0.8769
[Round 1] Purity: 0.7687
6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:11<00:00,  8.01it/s]


12058
=== Evaluation Round 2 ===
[Round 2] NMI: 0.8997
[Round 2] Purity: 0.8161
6029
12058


...

12058
=== Evaluation Round 3 ===
[Round 3] NMI: 0.8770
[Round 3] Purity: 0.7917
6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:11<00:00,  7.99it/s]


12058
=== Evaluation Round 4 ===
[Round 4] NMI: 0.8713
[Round 4] Purity: 0.7744
6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:11<00:00,  7.93it/s]


12058
=== Evaluation Round 5 ===
[Round 5] NMI: 0.8639
[Round 5] Purity: 0.7498

Average NMI: 0.8778 ± 0.0120
Average Purity: 0.7801 ± 0.0224


In [ ]:
n_rounds = 5
nmis, purity_scores = [], []
label_encoder = LabelEncoder()

for i in range(n_rounds):
  # Step 1: Sample non-existing to balance
  sampled_negatives = random.sample(ne_full_triples, len(full_triples))
  combined_triples = full_triples + sampled_negatives
  label_ids = [0]*len(full_triples) + [1]*len(sampled_negatives)
  print(len(sampled_negatives))
  print(len(combined_triples))
  # Step 2: Get embeddings
  # embeddings = model.encode(combined_triples)  # model must return numpy array
  X,_, y = extract_relation_embeddings(
    triples = combined_triples,
    tokenizer = tokenizer,
    model = model,
    batch_size=128,
    device="cuda"
)

  label_ids = label_encoder.fit_transform(y)
  print(len(y))

  # Step 3: Evaluate using your provided function
  print(f"=== Evaluation Round {i+1} ===")
  nmi, purity = evaluate_embeddings(X, y, label_ids, title=f"Round {i+1}")

  # # Step 4: Optional metric collection for averaging
  # embeddings_gpu = cp.asarray(embeddings)
  # kmeans = KMeans(n_clusters=2, random_state=42)
  # kmeans.fit(embeddings_gpu)
  # cluster_labels = kmeans.labels_.get()

  # nmi = normalized_mutual_info_score(label_ids, cluster_labels)
  # cm = ClusteringMetric(label_ids, cluster_labels)
  # purity = cm.purity_score()

  nmis.append(nmi)
  purity_scores.append(purity)

# Final aggregated metrics
print(f"\nAverage NMI: {np.mean(nmis):.4f} ± {np.std(nmis):.4f}")
print(f"Average Purity: {np.mean(purity_scores):.4f} ± {np.std(purity_scores):.4f}")

6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:19<00:00,  4.79it/s]


12058
=== Evaluation Round 1 ===
num_clusters 45
[Round 1] NMI: 0.8897
[Round 1] Purity: 0.8137
6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:19<00:00,  4.77it/s]


12058
=== Evaluation Round 2 ===
num_clusters 45
[Round 2] NMI: 0.8633
[Round 2] Purity: 0.7676
6029
12058


...

12058
=== Evaluation Round 3 ===
num_clusters 45
[Round 3] NMI: 0.8735
[Round 3] Purity: 0.7748
6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:19<00:00,  4.80it/s]


12058
=== Evaluation Round 4 ===
num_clusters 45
[Round 4] NMI: 0.8801
[Round 4] Purity: 0.7816
6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:19<00:00,  4.78it/s]

12058
=== Evaluation Round 5 ===
num_clusters 45
[Round 5] NMI: 0.8867
[Round 5] Purity: 0.7980

Average NMI: 0.8787 ± 0.0095
Average Purity: 0.7871 ± 0.0166


# Sampling Masked relations

In [ ]:
n_rounds = 5
nmis, purity_scores = [], []
label_encoder = LabelEncoder()

for i in range(n_rounds):
  # Step 1: Sample non-existing to balance
  sampled_negatives = random.sample(ne_full_triples, len(full_triples))
  combined_triples = full_triples + sampled_negatives
  label_ids = [0]*len(full_triples) + [1]*len(sampled_negatives)
  print(len(sampled_negatives))
  print(len(combined_triples))
  # Step 2: Get embeddings
  # embeddings = model.encode(combined_triples)  # model must return numpy array
  _, masked_X, y = extract_relation_embeddings(
    triples = combined_triples,
    tokenizer = tokenizer,
    model = model,
    batch_size=128,
    device="cuda"
)

  label_ids = label_encoder.fit_transform(y)
  print(len(y))

  # Step 3: Evaluate using your provided function
  print(f"=== Evaluation Round {i+1} ===")
  nmi, purity = evaluate_embeddings(masked_X, y, label_ids, title=f"Round {i+1}")

  # # Step 4: Optional metric collection for averaging
  # embeddings_gpu = cp.asarray(embeddings)
  # kmeans = KMeans(n_clusters=2, random_state=42)
  # kmeans.fit(embeddings_gpu)
  # cluster_labels = kmeans.labels_.get()

  # nmi = normalized_mutual_info_score(label_ids, cluster_labels)
  # cm = ClusteringMetric(label_ids, cluster_labels)
  # purity = cm.purity_score()

  nmis.append(nmi)
  purity_scores.append(purity)

# Final aggregated metrics
print(f"\nAverage NMI: {np.mean(nmis):.4f} ± {np.std(nmis):.4f}")
print(f"Average Purity: {np.mean(purity_scores):.4f} ± {np.std(purity_scores):.4f}")

6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:20<00:00,  4.73it/s]


12058
=== Evaluation Round 1 ===
num_clusters 45
[Round 1] NMI: 0.1174
[Round 1] Purity: 0.1588
6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:20<00:00,  4.58it/s]


12058
=== Evaluation Round 2 ===
num_clusters 45
[Round 2] NMI: 0.1213
[Round 2] Purity: 0.1503
6029
12058


...

12058
=== Evaluation Round 3 ===
num_clusters 45
[Round 3] NMI: 0.1288
[Round 3] Purity: 0.1538
6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:19<00:00,  4.79it/s]


12058
=== Evaluation Round 4 ===
num_clusters 45
[Round 4] NMI: 0.1233
[Round 4] Purity: 0.1407
6029
12058


Extracting embeddings: 100%|██████████| 95/95 [00:19<00:00,  4.80it/s]

12058
=== Evaluation Round 5 ===
num_clusters 45
[Round 5] NMI: 0.1247
[Round 5] Purity: 0.1455

Average NMI: 0.1231 ± 0.0038
Average Purity: 0.1498 ± 0.0063


In [ ]:
print(len(set(y)))

45


# Sampling (Core triples)

In [ ]:
n_rounds = 5
nmis, purity_scores = [], []
label_encoder = LabelEncoder()

for i in range(n_rounds):
  # Step 1: Sample non-existing to balance
  sampled_negatives = random.sample(ne_core_rel_triples, len(core_rel_triples))
  combined_triples = core_rel_triples + sampled_negatives
  label_ids = [0]*len(core_rel_triples) + [1]*len(sampled_negatives)
  print(len(sampled_negatives))
  print(len(combined_triples))
  # Step 2: Get embeddings
  # embeddings = model.encode(combined_triples)  # model must return numpy array
  X_core, y_core = extract_relation_embeddings(
    triples = combined_triples,
    tokenizer = tokenizer,
    model = model,
    batch_size=128,
    device="cuda"
)

  core_label_ids = label_encoder.fit_transform(y_core)

  # Step 3: Evaluate using your provided function
  print(f"=== Evaluation Round {i+1} ===")
  nmi, purity = evaluate_embeddings(X_core, y_core, core_label_ids, title=f"Round {i+1}")

  # # Step 4: Optional metric collection for averaging
  # embeddings_gpu = cp.asarray(embeddings)
  # kmeans = KMeans(n_clusters=2, random_state=42)
  # kmeans.fit(embeddings_gpu)
  # cluster_labels = kmeans.labels_.get()

  # nmi = normalized_mutual_info_score(label_ids, cluster_labels)
  # cm = ClusteringMetric(label_ids, cluster_labels)
  # purity = cm.purity_score()

  nmis.append(nmi)
  purity_scores.append(purity)

# Final aggregated metrics
print(f"\nAverage NMI: {np.mean(nmis):.4f} ± {np.std(nmis):.4f}")
print(f"Average Purity: {np.mean(purity_scores):.4f} ± {np.std(purity_scores):.4f}")

5940
11880


Extracting embeddings: 100%|██████████| 93/93 [00:11<00:00,  7.95it/s]


=== Evaluation Round 1 ===
[Round 1] NMI: 0.8987
[Round 1] Purity: 0.8203
5940
11880


Extracting embeddings: 100%|██████████| 93/93 [00:11<00:00,  7.99it/s]


=== Evaluation Round 2 ===
[Round 2] NMI: 0.8741
[Round 2] Purity: 0.7636
5940
11880


...

=== Evaluation Round 3 ===
[Round 3] NMI: 0.8814
[Round 3] Purity: 0.8019
5940
11880


Extracting embeddings: 100%|██████████| 93/93 [00:11<00:00,  7.97it/s]


=== Evaluation Round 4 ===
[Round 4] NMI: 0.8901
[Round 4] Purity: 0.8072
5940
11880


Extracting embeddings: 100%|██████████| 93/93 [00:11<00:00,  7.98it/s]

=== Evaluation Round 5 ===
[Round 5] NMI: 0.9198
[Round 5] Purity: 0.8741

Average NMI: 0.8928 ± 0.0158
Average Purity: 0.8134 ± 0.0357


In [ ]:
print(len(set(y_core)))

41


In [ ]:
# Step 3: Label encoding
label_encoder = LabelEncoder()

at_label_ids = label_encoder.fit_transform(at_y)
at_core_label_ids = label_encoder.fit_transform(at_y_core)


# Step 5: Run Evaluation
evaluate_embeddings(at_X_full, at_y, at_label_ids, title="All_triples_Full Relation")
print("")
evaluate_embeddings(at_X_core, at_y_core, at_core_label_ids, title="All_triples_Core Relation Only")

print("")
evaluate_embeddings(at_X_masked, at_y, at_label_ids, title="All_triples_Masked Relation")
print("")

label_ids 6029
core_label_ids 5940



/usr/local/lib/python3.11/dist-packages/cuml/internals/api_decorators.py:195: FutureWarning: The default value of `n_init` will change from 1 to 'auto' in 25.04. Set the value of `n_init` explicitly to suppress this warning.
  return func(*args, **kwargs)


[All_triples_Full Relation] NMI: 0.9418
[All_triples_Full Relation] Purity: 0.9281



/usr/local/lib/python3.11/dist-packages/cuml/internals/api_decorators.py:195: FutureWarning: The default value of `n_init` will change from 1 to 'auto' in 25.04. Set the value of `n_init` explicitly to suppress this warning.
  return func(*args, **kwargs)


[All_triples_Core Relation Only] NMI: 0.9638
[All_triples_Core Relation Only] Purity: 0.9547

[All_triples_Masked Relation] NMI: 0.0000
[All_triples_Masked Relation] Purity: 0.0451



/usr/local/lib/python3.11/dist-packages/cuml/internals/api_decorators.py:195: FutureWarning: The default value of `n_init` will change from 1 to 'auto' in 25.04. Set the value of `n_init` explicitly to suppress this warning.
  return func(*args, **kwargs)


In [ ]:
all_triples_relation_labels = [r for _, r, _ in at_full_triples]
all_triples_core_relation_labels = [r for _, r, _ in at_core_rel_triples]

# all_triples_relation_labels = [r for _, r, _ in all_triples]

all_triples_Relations = set(list(all_triples_relation_labels))

all_triples_relations = [r for r in all_triples_Relations if r != 'isa']  # Exclude 'isa'

# print('label_ids', len(at_label_ids))
# print('core_label_ids', len(at_core_label_ids))
# print("")

In [ ]:
print(len(set(list(all_triples_relation_labels))))
print(len(set(list(all_triples_core_relation_labels))))


45
41


# Existing + BERT_Prediction (Full Relation)


In [ ]:
existing_BERT_triples = full_triples + bert_prediction_triples
print(len(existing_BERT_triples))

12058


In [ ]:
print(len(bert_prediction_triples))

6029


In [ ]:
def evaluate_embeddings_existing_bert(embeddings, labels, label_ids, title=""):
    embeddings_gpu = cp.asarray(embeddings)
    num_clusters = 45
    kmeans = KMeans(n_clusters=num_clusters, random_state=42, max_iter=300)
    kmeans.fit(embeddings_gpu)
    cluster_labels = kmeans.labels_

    # Convert to CPU numpy
    cluster_labels_np = cluster_labels.get()

    # NMI
    nmi = normalized_mutual_info_score(label_ids, cluster_labels_np)

    # Purity (using your ClusteringMetric class)
    cm = ClusteringMetric(label_ids, cluster_labels_np)
    purity = cm.purity_score()

    # Silhouette
    # sil_score = silhouette_score(embeddings_gpu, cluster_labels_np)

    print(f"[{title}] NMI: {nmi:.4f}")
    print(f"[{title}] Purity: {purity:.4f}")
    # print(f"[{title}] Silhouette: {sil_score:.4f}\n")

    return nmi, purity

In [ ]:
print(len(y))

12058


In [ ]:
X_full, _, y = extract_relation_embeddings(
    triples = existing_BERT_triples,
    tokenizer = tokenizer,
    model = model,
    batch_size=128,
    device="cuda"
)


# Step 3: Label encoding
label_encoder = LabelEncoder()

label_ids = label_encoder.fit_transform(y)

print('label_ids', len(label_ids))
print("")

# Step 5: Run Evaluation
print('label_ids', len(label_ids), 'num_of_relations', 45)
evaluate_embeddings_existing_bert(X_full, y, label_ids, title="Full Relation")
print("")
# evaluate_embeddings(X_core, y_core, core_label_ids, title="Core Relation Only")


print('label_ids', len(label_ids), 'num_of_relations', len(set(list(label_ids))))
evaluate_embeddings(X_full, y, label_ids, title="Full Relation")

# print("")
# evaluate_embeddings(X_masked, y, label_ids, title="Masked Relation")
# print("")

Extracting embeddings: 100%|██████████| 95/95 [00:20<00:00,  4.59it/s]


label_ids 12058

label_ids 12058 num_of_relations 45
[Full Relation] NMI: 0.8599
[Full Relation] Purity: 0.8045

label_ids 12058 num_of_relations 284
[Full Relation] NMI: 0.8047
[Full Relation] Purity: 0.3607


(np.float64(0.8047049428779518), np.float64(0.36067341184275997))

In [ ]:
X_full, _, y = extract_relation_embeddings(
    triples = existing_BERT_triples,
    tokenizer = tokenizer,
    model = model,
    batch_size=128,
    device="cuda"
)


# Step 3: Label encoding
label_encoder = LabelEncoder()

label_ids = label_encoder.fit_transform(y)

print('label_ids', len(label_ids))
print("")

# Step 5: Run Evaluation
print('label_ids', len(label_ids), 'num_of_relations', 45)
evaluate_embeddings_existing_bert(X_full, y, label_ids, title="Full Relation")
print("")
# evaluate_embeddings(X_core, y_core, core_label_ids, title="Core Relation Only")


print('label_ids', len(label_ids), 'num_of_relations', len(set(list(label_ids))))
evaluate_embeddings(X_full, y, label_ids, title="Full Relation")

# print("")
# evaluate_embeddings(X_masked, y, label_ids, title="Masked Relation")
# print("")

Extracting embeddings: 100%|██████████| 95/95 [00:19<00:00,  4.83it/s]


label_ids 12058

label_ids 12058 num_of_relations 45
[Full Relation] NMI: 0.8599
[Full Relation] Purity: 0.8045

label_ids 12058 num_of_relations 284
num_clusters 284
[Full Relation] NMI: 0.8047
[Full Relation] Purity: 0.3607


(np.float64(0.8047049428779518), np.float64(0.36067341184275997))

In [ ]:
print(len(set(label_ids)))

284


# Existing + BERT_Prediction (Core Relation)


In [ ]:
BERT_PREDICT_core = []
BERT_PREDICT_core_2= []
# Setup
fill_mask = pipeline("fill-mask", model="bert-base-uncased", device=0 if torch.cuda.is_available() else -1)
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased')
model = BertModel.from_pretrained('bert-base-uncased').to(device)

def clean_text(text):
    return text.replace("_", " ")

# === STEP 1: Prepare triples ===
print("🔍 Step 1: Collecting (subject, object) → [relations] mapping...")
pair_to_rels = defaultdict(list)
for subj, rel, obj in core_rel_triples:
  pair_to_rels[(clean_text(subj), clean_text(obj))].append(clean_text(rel))

print(f"✅ Total unique (subject, object) pairs: {len(pair_to_rels)}")

def encode_sentence(text):
  with torch.no_grad():
    inputs = tokenizer(text, return_tensors="pt", truncation=True, padding=True).to(device)
    outputs = model(**inputs)
    return outputs.last_hidden_state.mean(dim=1).squeeze().cpu().numpy()

X_embed = []
y_true = []
pred_tokens = []

max_print_samples = 5
printed_samples = 0

for (subj, obj), rels in tqdm(pair_to_rels.items(), desc="Processing pairs"):
    top_k = len(set(rels))
    mask_prompt = f"{subj} {fill_mask.tokenizer.mask_token} {obj}"

    try:
        predictions = fill_mask(mask_prompt, top_k=top_k)
    except Exception as e:
        print(f"⚠️  Error on: {mask_prompt}")
        continue

    if printed_samples < max_print_samples:
        print(f"\n📎 Input: {mask_prompt}")
        print(f"🔮 Top-{top_k} predicted tokens: {[p['token_str'].strip() for p in predictions]}")
        print(f"🎯 Ground-truth relations: {rels}")

    for pred in predictions:
        token = pred["token_str"].strip()
        sentence = f"{subj} {token} {obj}"
        emb = encode_sentence(sentence)

        if printed_samples < max_print_samples:
            print(f"📘 Encoded Sentence: {sentence}")
            printed_samples += 1
        X_embed.append(emb)
        y_true.append(clean_text(rels[0]))
        pred_tokens.append(token)
        BERT_PREDICT_core.append([subj, token, obj])


Some weights of the model checkpoint at bert-base-uncased were not used when initializing BertForMaskedLM: ['bert.pooler.dense.bias', 'bert.pooler.dense.weight', 'cls.seq_relationship.bias', 'cls.seq_relationship.weight']
- This IS expected if you are initializing BertForMaskedLM from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertForMaskedLM from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Device set to use cuda:0


🔍 Step 1: Collecting (subject, object) → [relations] mapping...
✅ Total unique (subject, object) pairs: 3776


Processing pairs:   0%|          | 1/3776 [00:01<1:34:54,  1.51s/it]


📎 Input: diagnostic procedure [MASK] occupation or discipline
🔮 Top-2 predicted tokens: [':', '-']
🎯 Ground-truth relations: ['method of', 'issue in']
📘 Encoded Sentence: diagnostic procedure : occupation or discipline
📘 Encoded Sentence: diagnostic procedure - occupation or discipline

📎 Input: molecular biology research technique [MASK] mental process
🔮 Top-2 predicted tokens: [':', 'of']
🎯 Ground-truth relations: ['affects', 'measures']
📘 Encoded Sentence: molecular biology research technique : mental process
📘 Encoded Sentence: molecular biology research technique of mental process

📎 Input: mental process [MASK] behavior
🔮 Top-2 predicted tokens: ['and', 'mental']
🎯 Ground-truth relations: ['result of', 'affects']
📘 Encoded Sentence: mental process and behavior


Processing pairs: 100%|██████████| 3776/3776 [01:31<00:00, 41.11it/s]


In [ ]:
with open("bert_predict_core.json", "w", encoding="utf-8") as f:
    json.dump(BERT_PREDICT_core, f, ensure_ascii=False, indent=2)
print(len(BERT_PREDICT_core))

5940


In [ ]:
with open("bert_predict_core.json", "r", encoding="utf-8") as f:
    bbbb = json.load(f)

In [ ]:
print(bbbb[:3])
print(BERT_PREDICT_core[:3])

print(len(set(y_true)))

[['diagnostic procedure', ':', 'occupation or discipline'], ['diagnostic procedure', '-', 'occupation or discipline'], ['molecular biology research technique', ':', 'mental process']]
[['diagnostic procedure', ':', 'occupation or discipline'], ['diagnostic procedure', '-', 'occupation or discipline'], ['molecular biology research technique', ':', 'mental process']]
40


In [ ]:
print(len(set(pred_tokens)))

238


In [ ]:
core_existing_BERT_triples = core_rel_triples + BERT_PREDICT_core


In [ ]:
core_rel_triples_2 = []
for j in core_rel_triples:
  core_rel_triples_2.append(j)

In [ ]:
print(BERT_PREDICT_core[:3])
print(BERT_PREDICT_core_2[:3])
print(core_rel_triples[:3])

[['diagnostic procedure', ':', 'occupation or discipline'], ['diagnostic procedure', '-', 'occupation or discipline'], ['molecular biology research technique', ':', 'mental process']]
[]
[['diagnostic_procedure', 'method_of', 'occupation_or_discipline'], ['molecular_biology_research_technique', 'affects', 'mental_process'], ['mental_process', 'result_of', 'behavior']]


In [ ]:
for j in :

  # Find positions of subject and object
subj_idx = full_text.find(subj)
obj_idx = full_text.find(obj)

# First part: everything from start up to token
before = full_text[:subj_idx].strip() + ' ' + subj
middle = token.strip()
after = full_text[obj_idx:].strip()

# Result
split_parts = [before.strip(), middle, after.strip()]

In [ ]:
print(len(core_existing_BERT_triples))

11880


In [ ]:
def evaluate_embeddings_core_existing_bert(embeddings, labels, label_ids, title=""):
    embeddings_gpu = cp.asarray(embeddings)
    num_clusters = 279
    kmeans = KMeans(n_clusters=num_clusters, random_state=42, max_iter=300)
    kmeans.fit(embeddings_gpu)
    cluster_labels = kmeans.labels_

    # Convert to CPU numpy
    cluster_labels_np = cluster_labels.get()

    # NMI
    nmi = normalized_mutual_info_score(label_ids, cluster_labels_np)

    # Purity (using your ClusteringMetric class)
    cm = ClusteringMetric(label_ids, cluster_labels_np)
    purity = cm.purity_score()

    # Silhouette
    # sil_score = silhouette_score(embeddings_gpu, cluster_labels_np)

    print(f"[{title}] NMI: {nmi:.4f}")
    print(f"[{title}] Purity: {purity:.4f}")
    # print(f"[{title}] Silhouette: {sil_score:.4f}\n")

    return nmi, purity

In [ ]:
X_core, _, y_core = extract_relation_embeddings(
    triples = core_existing_BERT_triples,
    tokenizer = tokenizer,
    model = model,
    batch_size=128,
    device="cuda"
)


# Step 3: Label encoding
label_encoder = LabelEncoder()

core_label_ids = label_encoder.fit_transform(y_core)

print('label_ids', len(core_label_ids))
print("")

# Step 5: Run Evaluation
print('label_ids', len(core_label_ids), 'num_of_relations', 40)
evaluate_embeddings_core_existing_bert(X_core, y_core, core_label_ids, title="Core Relation")
print("")
# evaluate_embeddings(X_core, y_core, core_label_ids, title="Core Relation Only")


print('label_ids', len(label_ids), 'num_of_relations', len(set(list(label_ids))))
evaluate_embeddings(X_core, y_core, core_label_ids, title="Core Relation_BERT")

# print("")
# evaluate_embeddings(X_masked, y, label_ids, title="Masked Relation")
# print("")

Extracting embeddings: 100%|██████████| 93/93 [00:19<00:00,  4.66it/s]


label_ids 11880

label_ids 11880 num_of_relations 40
[Core Relation] NMI: 0.8475
[Core Relation] Purity: 0.8162

label_ids 12058 num_of_relations 284
num_clusters 278
[Core Relation_BERT] NMI: 0.8051
[Core Relation_BERT] Purity: 0.3682


(np.float64(0.805117689042513), np.float64(0.36818181818181817))

In [ ]:
# Step 5: Run Evaluation
print('label_ids', len(core_label_ids), 'num_of_relations', 41)
evaluate_embeddings_core_existing_bert(X_core, y_core, core_label_ids, title="Core Relation")

label_ids 11880 num_of_relations 41
[Core Relation] NMI: 0.8674
[Core Relation] Purity: 0.8451


(np.float64(0.8674157469040239), np.float64(0.8451178451178452))

In [ ]:
evaluate_embeddings_core_existing_bert(X_core, y_core, core_label_ids, title="Core Relation")

[Core Relation] NMI: 0.8071
[Core Relation] Purity: 0.3721


(np.float64(0.8071429576481935), np.float64(0.37213804713804716))